In [1]:
from geopandas import GeoDataFrame as df
import math
from shapely.geometry import LineString,Point
import json
%matplotlib inline
from geopandas import GeoSeries as ds
import pandas as pd

In [ ]:
#from shape generate lines

In [38]:
import csv
import os
import sys

filename = "mta_shapes_meters_historical_remapped.csv"
csv_columns = ['distance_per_id']
temp_csv_file = "temp.csv"

with open(filename) as f:
    csvReader = csv.reader(f)
    headers = next(csvReader)
    d = {}
    
    priorId = None
    priorAccuDist = None
    priorStop = None

    with open(temp_csv_file, 'w') as csvfile:
        writer = csv.writer(csvfile, dialect='excel', quoting=csv.QUOTE_NONNUMERIC)
        writer.writerow(csv_columns)
    
        for row in csvReader:
    
            fullId = row[0]+'-'+row[1]
            currentId = row[0]
            currentAccuDist = float(row[2])
            currentStop = row[3]

            if priorId == currentId:
                distEach = currentAccuDist - priorAccuDist
                writer.writerow([distEach])
                priorAccuDist = currentAccuDist
                priorStop = currentStop

            else:
                priorId = currentId
                priorAccuDist = currentAccuDist
                priorStop = currentStop
                writer.writerow([0])

#from shape generate lines

In [3]:
shapes = df.from_csv('all_city/shapes.txt',index_col=None)
#shapes.head()
shapes['shape_seq']=shapes['shape_pt_sequence'].apply(lambda x: math.floor(x/10000))
shapes['shape_seq_id']=shapes[['shape_id','shape_seq']].apply(lambda x:str(x[0])+'-'+str(int(x[1])),axis=1)
shapes.head()

shape_id  shape_pt_lat  shape_pt_lon  shape_pt_sequence  shape_seq  \
0   B10149     40.578199    -73.939756              10001          1   
1   B10149     40.578209    -73.939756              10002          1   
2   B10149     40.578209    -73.939756              20001          2   
3   B10149     40.578263    -73.939756              20002          2   
4   B10149     40.578378    -73.939814              20003          2   

  shape_seq_id  
0     B10149-1  
1     B10149-1  
2     B10149-2  
3     B10149-2  
4     B10149-2

In [18]:
trips=df.from_csv('all_city/trips_historical_min.csv',index_col=None)
trips.head()

route_id                            trip_headsign  direction_id shape_id
0       B6                             ROCK PKY STA             0   B60169
1       B6                     AVENUE J CONEY IS AV             1   B60171
2      B41       DNTWN BKLYN CADMAN PLZ via FLATBSH             0  B410308
3      B41  LTD DNTWN BKLYN CADMAN PLZ via FLATBUSH             0  B410310
4      B41       DNTWN BKLYN CADMAN PLZ via FLATBSH             0  B410312

In [19]:
distances=df.from_csv('mta_shapes_meters_historical_remapped.csv',index_col=None)
distances['full_id']=distances[['shape_id','sequence_id']].apply(lambda x:str(x[0])+'-'+str(int(x[1])),axis=1)
distances.head()

shape_id  sequence_id  meters  stop_id  distance_per_id     full_id
0  B1000031            1     0.0   308452              0.0  B1000031-1
1  B1000031            2    94.6   350129             94.6  B1000031-2
2  B1000031            3   585.1   350217            490.5  B1000031-3
3  B1000031            4   958.1   350158            373.0  B1000031-4
4  B1000031            5  1404.9   303920            446.8  B1000031-5

In [20]:
speeds=df.from_csv('all_city/speed.csv',sep='\t',header=None,index_col=None)
speeds.columns = ['key', 'speed']
speeds['full_id']=speeds['key'].apply(lambda x: x.split('|')[0])
speeds['stop_id']=speeds['key'].apply(lambda x: x.split('|')[1])
speeds.head()

key     speed      full_id stop_id
0  B1000057-10|350132  5.052191  B1000057-10  350132
1  B1000057-11|350110  5.745421  B1000057-11  350110
2  B1000057-12|350126  1.981738  B1000057-12  350126
3  B1000057-13|350117  5.727091  B1000057-13  350117
4  B1000057-14|350119  6.772595  B1000057-14  350119

In [31]:
line_dict={}
counter = 0

#debug
inJFILE = set()
notInJFILE = set()

for shape_id in set(speeds.full_id):
#shape_id = 'B1000057-10'
#if shape_id:
    #try
    speed = float(speeds.loc[speeds['full_id'] == shape_id].speed)
    distance = float(distances.loc[distances['full_id'] == shape_id].distance_per_id)
    stop = int(distances.loc[distances['full_id'] == shape_id].stop_id )
    shape_num = shape_id.split('-')[0]
    seq = shape_id.split('-')[1]

    #debug Jiamin File===
    if route_name or route_id:
        inJFILE.add(shape_num)
    else:
        notInJFILE.add(shape_num)
    #====================
    
    if shape_num not in line_dict:
        line_dict[shape_num]={}
    line_dict[shape_num][seq]={}    
    line_dict[shape_num][seq]['speed']=speed
    line_dict[shape_num][seq]['distance']=distance
    line_dict[shape_num][seq]['stop_id']=stop

    if ('route_name' not in line_dict[shape_num]) or ('route_id' not in line_dict[shape_num]):        
        route_name = list(set(trips.loc[trips['shape_id'] == shape_num].trip_headsign))
        route_id = list(set(trips.loc[trips['shape_id'] == shape_num].route_id))         
        line_dict[shape_num]['route_name']=route_name
        line_dict[shape_num]['route_id']=route_id
    else:
        pass
    
    if 'list_stop_id' not in line_dict[shape_num]:
        line_dict[shape_num]['list_stop_id'] = list(distances.loc[distances['shape_id'] == shape_num].stop_id)
        line_dict[shape_num]['distance_per_id'] = list(distances.loc[distances['shape_id'] == shape_num].distance_per_id) 
    else:
        pass
    
    #except:
    #    errorCounter += 1
    counter += 1
    if counter % 100 == 0:
        print counter
#     if errorCounter == 100:
#         break

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200
11300
11400
11500
11600
11700
11800
11900
12000
12100
12200
12300
12400
12500
12600
12700
12800
12900
13000
13100
13200
13300
13400
13500
13600
13700
13800
13900
14000
14100
14200
14300
14400
14500
14600
14700
14800
14900
15000
15100
15200
15300
15400
15500
15600
15700
15800
15900
16000
16100
16200
16300
16400
16500
16600
16700
16800
16900
17000
17100
17200
17300
17400
17500
17600
17700
17800
17900
18000
18100
18200
18300
18400
1850

In [32]:
print len(inJFILE)
print len(notInJFILE)
#print notInJFILE

1362
0


In [33]:
line_dict['B110025']

{'10': {'distance': 202.5, 'speed': 4.427232700446363, 'stop_id': 307479},
 '11': {'distance': 201.5, 'speed': 2.873036691059629, 'stop_id': 308576},
 '12': {'distance': 316.5, 'speed': 3.1123557668583413, 'stop_id': 307482},
 '13': {'distance': 325.7, 'speed': 7.287616031290367, 'stop_id': 306446},
 '14': {'distance': 158.5, 'speed': 5.193843027842521, 'stop_id': 301279},
 '15': {'distance': 171.0, 'speed': 5.9828108708998915, 'stop_id': 301280},
 '16': {'distance': 141.5, 'speed': 2.9895900937199205, 'stop_id': 301281},
 '17': {'distance': 252.3, 'speed': 6.764518201032993, 'stop_id': 301282},
 '18': {'distance': 127.6, 'speed': 1.7787159066664142, 'stop_id': 301283},
 '19': {'distance': 324.5, 'speed': 6.6795752177207754, 'stop_id': 308069},
 '2': {'distance': 375.5, 'speed': 0.9152905440876736, 'stop_id': 300636},
 '20': {'distance': 330.2, 'speed': 6.0267364865814566, 'stop_id': 300891},
 '21': {'distance': 161.8, 'speed': 4.2206558100471705, 'stop_id': 301286},
 '22': {'distance'

In [34]:
import cPickle as pickle
pickle.dump(line_dict, open( "line_dict.p", "wb" ))

In [2]:
import cPickle as pickle

pickinfile = open('line_dict.p','rb') 
line_dict = pickle.load(pickinfile)

In [14]:
line_dict['B110025']['25']['']

{'distance': 237.8, 'speed': 4.284963120487257, 'stop_id': 301290}

In [17]:
import heapq

d_ave_each = {}

counter = 0
for shapeid, v1 in line_dict.items():
#     if counter > 5 :
#         break
    for seq, v2 in v1.items():
        if seq != 'list_stop_id':
            try:
                rid = v1['route_id'][0]
                spd = v2['speed']
                if rid not in d_ave_each:
                    d_ave_each[rid] = [] 
                d_ave_each[rid].append(spd)     
            except:
                pass
    counter += 1

def nth_largest(iter):
    n = len(iter)/2
    return heapq.nlargest(n, iter)[-1]

d_ave_each_perRoute = {}
list_all_speed = []

for shapeid, spd_list in d_ave_each.items():
    if shapeid not in d_ave_each_perRoute:
        try:
            d_ave_each_perRoute[shapeid] = nth_largest(d_ave_each[shapeid])
            list_all_speed += d_ave_each[shapeid]
        except:
            pass
    else:
        pass
    
d_ave_each_perRoute_sorted = sorted(d_ave_each_perRoute.iteritems(), key=lambda x: (-x[1], x[0]), reverse=False)

top5hi = d_ave_each_perRoute_sorted[:5]
top5lo = d_ave_each_perRoute_sorted[-5:]

median_of_all = nth_largest(list_all_speed)
average_of_all = float(sum(list_all_speed))/len(list_all_speed)


In [21]:
average_of_all

6.785772688873981

#dump to redis

In [22]:
import redis
pool = redis.ConnectionPool(host='busvis.cloudapp.net', port=6379, db=11)
r = redis.Redis(connection_pool=pool)

In [23]:
for shapeid in line_dict:
    r.hset("speed_distance",shapeid, line_dict[shapeid])

In [24]:
r.hset('top5hi','top5hi', top5hi)
r.hset('top5lo','top5lo', top5lo)
r.hset('median','median_of_all',median_of_all)
r.hset('average','average_of_all',average_of_all)

for route in d_ave_each:
    r.hset("speed_per_route_list",route, d_ave_each[route]) 
    
for route in d_ave_each_perRoute:
    r.hset("speed_per_route_median",route, d_ave_each_perRoute[route]) 

    

#test

In [1]:
import redis
import ast 

pool = redis.ConnectionPool(host='busvis.cloudapp.net', port=6379, db=11)
r = redis.Redis(connection_pool=pool)
output = r.hget('speed_distance','B110025')
output =  ast.literal_eval(str(output))
output

In [9]:
import cPickle as pickle

pickinfile = open('line_dict.p','rb') 
pout = pickle.load(pickinfile)

EOFError: 

In [8]:
pout

{'Q280470': {'10': {'distance': 170.8,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL'],
   'speed': 1.3185805517322668,
   'stop_id': 503274},
  '11': {'distance': 96.8,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL'],
   'speed': 2.4383188691759448,
   'stop_id': 501719},
  '12': {'distance': 153.3,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL'],
   'speed': 0.3454590464364473,
   'stop_id': 501004},
  '13': {'distance': 166.7,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL'],
   'speed': 4.597006583501244,
   'stop_id': 501005},
  '14': {'distance': 197.2,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL'],
   'speed': 5.7245168920735665,
   'stop_id': 501722},
  '15': {'distance': 204.7,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL'],
   'speed': 12.653942585629633,
   'stop_id': 501723},
  '17': {'distance': 157.9,
   'route_id': ['Q28'],
   'route_name': ['BAY TERRACE  BELL BL